In [ ]:
# Activate virtual environment:
    # py -m venv venv
    # venv/Scripts/activate

# Installed: dash, pandas, numpy, jupyter-dash, plotly

In [1]:
# Import libraries

import psycopg2
import pandas as pd
import numpy as np
import plotly.express as px

#import plotly.graph_objects as go
#import scipy as sp
#import scipy.fftpack
#import datetime
#from numpy.fft import fft, ifft

from scipy.fftpack import rfft, rfftfreq, next_fast_len
from scipy.signal import find_peaks, peak_prominences
from dash import Dash, html, dcc

pd.options.plotting.backend = "plotly"

In [2]:
# Establish connection with database

CONNECTION_REMOTE = "postgres://nellis_read_only@fdh-shmdb.fdh-is.com:5432/nellis_data"
conn = psycopg2.connect(CONNECTION_REMOTE)
print("Connection successful!")

Connection successful!


In [3]:
# Custom functions

def drop_duplicate_indices(df):
    df = df.drop_duplicates(subset='time')
    df = df.set_index('time')
    return df

# 1) ADD FFT FUNCTION [RETURNS FREQ AND PEAKS AND % INFLUENCE], 2) ADD MODE DETERMINATION FUNCTION

In [4]:
### TEST CELLS ###

In [5]:
start_time = '2022-03-27 17:00:00'
end_time = '2022-03-27 18:00:00'
pole_id_A = '34'
pole_id_B = '35'

sts_accel_A = pd.read_sql(f"SELECT * FROM sts_acceleration WHERE time >= '{start_time}' AND time < '{end_time}' AND id = '{pole_id_A}' ORDER BY time", conn) 
drop_duplicate_indices(sts_accel_A)


accel_x   accel_y  accel_resultant  id
time                                                            
2022-03-27 17:00:00.018  0.012247 -0.006067         0.013667  34
2022-03-27 17:00:00.068  0.015153 -0.003334         0.015516  34
2022-03-27 17:00:00.118  0.012655  0.000755         0.012677  34
2022-03-27 17:00:00.168  0.008943  0.007791         0.011860  34
2022-03-27 17:00:00.218  0.010962  0.007617         0.013349  34
...                           ...       ...              ...  ..
2022-03-27 17:59:59.784  0.006445  0.001264         0.006567  34
2022-03-27 17:59:59.834  0.003600  0.004568         0.005816  34
2022-03-27 17:59:59.884  0.006883  0.004456         0.008200  34
2022-03-27 17:59:59.934  0.010891  0.000744         0.010916  34
2022-03-27 17:59:59.984  0.011472  0.006078         0.012982  34

[71981 rows x 4 columns]

In [6]:
df_sample = sts_accel_A     # Measurement to FFT = Function Input
df_field = 'accel_x'    # Field to SST - Function Input
dt = 1/20   # Data at 20 Hz per STS - Function Input

arr = df_sample.loc[:, [df_field]]
arr = arr[df_field].to_numpy()

yf = rfft(arr, next_fast_len(len(arr)))
xf = rfftfreq(next_fast_len(len(arr)), dt)

power = yf * np.conj(yf) / next_fast_len(len(arr))
freq = xf

fig = px.line( 
    None, 
    x = freq,
    y = np.abs(power),
    template = "plotly_dark",
)

fig.update_traces(
    line_color='yellow',
)

fig.update_layout(
    title = "FFT - Frequency Domain",
    xaxis_title="Frequency",
    yaxis_title="Power",
    xaxis = dict(tickformat = '.2f', showgrid = True),
    yaxis = dict(tickformat = '.2f', showgrid = True),
)

#%timeit rfft(f, next_fast_len(len(arr)))

In [7]:
# FIND PEAKS WITH THRESHOLD & COMPUTE CONTRIBUTION

Y = np.abs(power)
threshold = 3*np.std(Y) + np.mean(Y)    # 3 x Standard Deviation + Arithmetic Mean
distance = (len(freq)/max(freq))*0.25    # Number of horizontal points per 0.25 Hz

peaks, _ = find_peaks(power, threshold = threshold, distance = distance)

arrPower = Y[peaks]
arrFrequency = freq[peaks]

arrContribution = np.empty(len(arrPower))
sum_power = sum(arrPower)

for i in range(len(arrPower)):
    arrContribution[i] = arrPower[i] / sum_power

arrResults = np.column_stack((arrPower, arrFrequency, arrContribution))

print(arrResults)


[[1.46057680e-01 3.56944444e-01 7.80879564e-01]
 [3.62666793e-02 1.62527778e+00 1.93895375e-01]
 [4.71815886e-03 6.63527778e+00 2.52250606e-02]]


NEED TWO PROCESEES: 

1) IF WE KNOW MODAL RESPONSE
    - PULL IN THE MODE SHAPES, DEVELOP THE MODE 'WINDOWS', FIGURE OUT WHAT MODE EACH PEAK IS ON. 
2) IF WE DONT KNOW MODAL RESPONSE
    - PULL IN THE PEAKS, ASSUME A MINIMUM DISTANCE REQUIRED BETWEEN MODES, ASSIGN MODE WINDOWS FROM THERE. 



In [ ]:
### TEST CELLS ###

In [ ]:
# Select test window and pole

start_time = '2022-03-27 00:00:00'
end_time = '2022-03-28 00:00:00'
pole_id_A = '34'
pole_id_B = '35'

In [ ]:
# Query weather data

weather = pd.read_sql(f"SELECT * FROM weather WHERE time >= '{start_time}' AND time < '{end_time}' ORDER BY time", conn)
weather = drop_duplicate_indices(weather)
weather.head()

In [ ]:
# Query acceleration data

accl_A = pd.read_sql(f"SELECT * FROM sts_acceleration WHERE time >= '{start_time}' AND time < '{end_time}' AND id = '{pole_id_A}' ORDER BY time", conn) 
accl_A = drop_duplicate_indices(accl_A)
accl_A.head()

accl_B = pd.read_sql(f"SELECT * FROM sts_acceleration WHERE time >= '{start_time}' AND time < '{end_time}' AND id = '{pole_id_B}' ORDER BY time", conn) 
accl_B = drop_duplicate_indices(accl_B)
accl_B.head()

In [ ]:
# Query displacement data

disp_A = pd.read_sql(f"SELECT * FROM sts_displacement WHERE time >= '{start_time}' AND time < '{end_time}' AND id = '{pole_id_A}' ORDER BY time", conn) 
disp_A = drop_duplicate_indices(disp_A)
disp_A.head()

disp_B = pd.read_sql(f"SELECT * FROM sts_displacement WHERE time >= '{start_time}' AND time < '{end_time}' AND id = '{pole_id_B}' ORDER BY time", conn) 
disp_B = drop_duplicate_indices(disp_B)
disp_B.head()

In [ ]:
# Resample to 5 minute increments using mean values

accl_A = accl_A.resample('1S').mean()
accl_B = accl_B.resample('1S').mean()
disp_A = disp_A.resample('1S').mean()
disp_B = disp_B.resample('1S').mean()

In [ ]:
# Add dummy mode to acceleration and displacement data for test purposes

accl_A['mode'] = np.random.randint(1,3,size=len(accl_A))
accl_B['mode'] = np.random.randint(1,3,size=len(accl_B))
disp_A['mode'] = accl_A['mode']
disp_B['mode'] = accl_B['mode']

accl_A['id'] = pole_id_A
accl_B['id'] = pole_id_B
disp_A['id'] = pole_id_A
disp_B['id'] = pole_id_B


In [ ]:
# Vertically combine tables

accl = pd.concat([accl_A,accl_B])
disp = pd.concat([disp_A,disp_B])

In [ ]:
# 2D heat density plot

fig = px.density_heatmap(
    disp,
    x = 'id',
    y = 'disp_resultant',
    facet_col = 'mode',
    text_auto = True,
    template = "plotly_dark",
    title = "Mode vs Deflection Heat Map",
    )

fig.show()

In [ ]:
# Scatter plot

fig = px.scatter(
    disp,
    x = 'id',
    y = 'disp_resultant',
    color = 'mode',
    template = "plotly_dark",
    title = "Mode vs Deflection Scatter Plot",
    )

fig.show()

In [ ]:
# 3D Scatter plot

fig = px.scatter_3d(
    disp,
    x = 'disp_x',
    y = 'disp_y',
    z = disp.index,
    color = 'id',
    symbol = 'mode',
    template = "plotly_dark",
    title = "Deflection vs Time 3D Scatter Plot",
    )

fig.show()

In [ ]:
fig = px.bar_polar(
    weather, 
    height = 600,
    r = "wind_speed", 
    theta = "wind_direction", 
    color = "wind_gust", 
    template = "plotly_dark",
    color_discrete_sequence = px.colors.sequential.Plasma_r,
    )

fig.update_layout(
    title = 'Wind Speed Data',
    font_size = 14,
    legend_font_size = 14,
    #polar_radialaxis_ticksuffix = ' x',
    )

fig.show()

In [ ]:
fig = px.parallel_coordinates(
    weather,
    color = "wind_direction",
    dimensions = ['wind_gust', 'wind_speed', 'temp_f'],
    labels = {"wind_gust":"Wind Gust", "temp_f":"Temperature", "wind_speed":"Wind Speed", "wind_direction":"Wind Direction"},
    color_continuous_scale=px.colors.diverging.Tealrose,
    )

fig.show()

In [ ]:
fig = px.scatter_matrix(
    weather,
    dimensions = ['wind_gust', 'wind_speed', 'temp_f'],
    color = "wind_direction",
)

fig.show()